In [1]:
import osmnx as ox
import pandas as pd
import folium
from shapely.geometry import Point, Polygon, MultiPolygon

In [2]:
# Get the coordinates for Dublin, Ireland
location = ox.geocode('Dublin, Ireland')

In [3]:
location

(53.3498006, -6.2602964)

In [4]:
# Use OpenStreetMaps library to get all the recreational/tourist spots within a specified distance
distance = 25000  # Radius of 25 kilometers around the location
tags = {'amenity': True}
gdf = ox.geometries_from_point(location, tags=tags, dist=distance)

In [5]:
gdf.head()

access    amenity     created_by  fee  parking  \
element_type osmid                                                      
node         29403586     yes    parking  Potlatch 0.5d   no  surface   
             59998053     NaN  recycling            NaN  NaN      NaN   
             78514742     NaN   post_box            NaN  NaN      NaN   
             78514747     NaN        atm            NaN  NaN      NaN   
             107986833    NaN   post_box            NaN  NaN      NaN   

                                         geometry recycling:glass  \
element_type osmid                                                  
node         29403586   POINT (-6.29177 53.17470)             NaN   
             59998053   POINT (-6.32597 53.29687)             yes   
             78514742   POINT (-6.31990 53.29923)             NaN   
             78514747   POINT (-6.32149 53.29920)             NaN   
             107986833  POINT (-6.31012 53.31284)             NaN   

                       recycling_type operator operator:wikidata  ...  \
element_type osmid                                                ...   
node         29403586             NaN      NaN               NaN  ...   
             59998053       container      NaN               NaN  ...   
             78514742             NaN  An Post           Q482490  ...   
             78514747             NaN      NaN               NaN  ...   
             107986833            NaN  An Post           Q482490  ...   

                       check_date:fee rooms trade building:levels:underground  \
element_type osmid                                                              
node         29403586             NaN   NaN   NaN                         NaN   
             59998053             NaN   NaN   NaN                         NaN   
             78514742             NaN   NaN   NaN                         NaN   
             78514747             NaN   NaN   NaN                         NaN   
             107986833            NaN   NaN   NaN                         NaN   

                       abandoned building:shape recycling:aggregate  \
element_type osmid                                                    
node         29403586        NaN            NaN                 NaN   
             59998053        NaN            NaN                 NaN   
             78514742        NaN            NaN                 NaN   
             78514747        NaN            NaN                 NaN   
             107986833       NaN            NaN                 NaN   

                       old_name:1925 heating fee:covid19  
element_type osmid                                        
node         29403586            NaN     NaN         NaN  
             59998053            NaN     NaN         NaN  
             78514742            NaN     NaN         NaN  
             78514747            NaN     NaN         NaN  
             107986833           NaN     NaN         NaN  

[5 rows x 666 columns]

In [6]:
gdf['amenity'].unique()

array(['parking', 'recycling', 'post_box', 'atm', 'pub', 'fuel', 'police',
       'cinema', 'pharmacy', 'fast_food', 'social_facility',
       'community_centre', 'bicycle_parking', 'post_office', 'fountain',
       'restaurant', 'nightclub', 'cafe', 'arts_centre', 'theatre',
       'parking_entrance', 'drinking_water', 'events_venue',
       'kindergarten', 'bank', 'childcare', 'toilets', 'library',
       'bicycle_rental', 'marketplace', 'car_wash', 'car_rental', 'taxi',
       'bar', 'place_of_worship', 'studio', 'dentist', 'doctors', 'bench',
       'box_office', 'waste_basket', 'internet_cafe', 'telephone',
       'college', 'casino', 'veterinary', 'clinic', 'shelter', 'clock',
       'internet_access', 'school', 'charging_station', 'vending_machine',
       'music_school', 'training', 'stripclub', 'courthouse',
       'language_school', 'funeral_hall', 'parking_space',
       'conference_centre', 'grave_yard', 'loading_dock', 'monastery',
       'public_bookcase', 'ice_cream', 'h

In [7]:
rec_tourist_tags = ['restaurant', 'cafe', 'pub', 'bar', 'theatre', 'arts_centre', 'cinema', 'nightclub']

In [8]:
# Filter the data for the recreational/tourist spots in the same 25 Km radius
rec_tourist_spots = gdf[gdf['amenity'].isin(rec_tourist_tags)]

In [10]:
len(rec_tourist_spots)

3128

In [12]:
rec_tourist_spots.shape

(3128, 666)

In [13]:
rec_tourist_spots = pd.DataFrame(rec_tourist_spots)

# Remove all the columns which have less than 10% of the records populated
selected_columns = rec_tourist_spots.columns[rec_tourist_spots.count() > 0.1*len(rec_tourist_spots)]
filtered_data = rec_tourist_spots[selected_columns]

In [14]:
filtered_data.shape

(3128, 21)

In [15]:
filtered_data.head()

amenity                   geometry               name  \
element_type osmid                                                             
node         132814618     pub  POINT (-6.37740 53.35007)     Silver Granite   
             133193958     pub  POINT (-6.26059 53.33055)      The Barge Bar   
             136513945     pub  POINT (-6.51863 53.31813)           Mc Evoys   
             254949231  cinema  POINT (-6.39372 53.35211)  Vue Cinema Dublin   
             263366607     pub  POINT (-6.42389 53.34739)     The Penny Hill   

                            addr:street email opening_hours  \
element_type osmid                                            
node         132814618              NaN   NaN           NaN   
             133193958  Charlemont Mall   NaN           NaN   
             136513945              NaN   NaN           NaN   
             254949231              NaN   NaN           NaN   
             263366607      Castle Road   NaN           NaN   

                                                               phone  \
element_type osmid                                                     
node         132814618                                           NaN   
             133193958                                           NaN   
             136513945                                           NaN   
             254949231  https://www.myvue.com/cinema/dublin/whats-on   
             263366607                                           NaN   

                       wheelchair addr:city contact:facebook  ...  \
element_type osmid                                            ...   
node         132814618        NaN       NaN              NaN  ...   
             133193958    limited       NaN              NaN  ...   
             136513945        NaN       NaN              NaN  ...   
             254949231        yes       NaN       VueCinemas  ...   
             263366607        yes     Lucan              NaN  ...   

                       addr:country addr:county addr:postcode  \
element_type osmid                                              
node         132814618          NaN         NaN           NaN   
             133193958          NaN         NaN           NaN   
             136513945          NaN         NaN           NaN   
             254949231          NaN         NaN           NaN   
             263366607           IE      Dublin      K78 Y6P9   

                       addr:housenumber cuisine takeaway smoking  \
element_type osmid                                                 
node         132814618              NaN     NaN      NaN     NaN   
             133193958              NaN     NaN      NaN     NaN   
             136513945              NaN     NaN      NaN     NaN   
             254949231              NaN     NaN      NaN     NaN   
             263366607              NaN     NaN      NaN     NaN   

                       outdoor_seating building nodes  
element_type osmid                                     
node         132814618             NaN      NaN   NaN  
             133193958             NaN      NaN   NaN  
             136513945             NaN      NaN   NaN  
             254949231             NaN      NaN   NaN  
             263366607             NaN      NaN   NaN  

[5 rows x 21 columns]

In [16]:
filtered_data.columns

Index(['amenity', 'geometry', 'name', 'addr:street', 'email', 'opening_hours',
       'phone', 'wheelchair', 'addr:city', 'contact:facebook', 'website',
       'addr:country', 'addr:county', 'addr:postcode', 'addr:housenumber',
       'cuisine', 'takeaway', 'smoking', 'outdoor_seating', 'building',
       'nodes'],
      dtype='object')

In [17]:
# Pick only the features/columns which will be useful for our analysis 
filtered_data = filtered_data[['geometry', 'amenity', 'name', 'addr:street', 'addr:city']]

In [18]:
# Rename the column names for downstream use
filtered_data = filtered_data.rename(columns={'geometry': 'rec_tourist_spots_geometry', 
                                              'amenity': 'rec_tourist_spots_tag', 
                                              'name': 'rec_tourist_spots_address',
                                              'addr:street': 'rec_tourist_spots_street',
                                              'addr:city': 'rec_tourist_spots_city'})

# Save the data into a CSV file
filtered_data.to_csv('04_recreational_tourist_locations.csv', index=False)

In [19]:
filtered_data.head()

rec_tourist_spots_geometry rec_tourist_spots_tag  \
element_type osmid                                                        
node         132814618  POINT (-6.37740 53.35007)                   pub   
             133193958  POINT (-6.26059 53.33055)                   pub   
             136513945  POINT (-6.51863 53.31813)                   pub   
             254949231  POINT (-6.39372 53.35211)                cinema   
             263366607  POINT (-6.42389 53.34739)                   pub   

                       rec_tourist_spots_address rec_tourist_spots_street  \
element_type osmid                                                          
node         132814618            Silver Granite                      NaN   
             133193958             The Barge Bar          Charlemont Mall   
             136513945                  Mc Evoys                      NaN   
             254949231         Vue Cinema Dublin                      NaN   
             263366607            The Penny Hill              Castle Road   

                       rec_tourist_spots_city  
element_type osmid                             
node         132814618                    NaN  
             133193958                    NaN  
             136513945                    NaN  
             254949231                    NaN  
             263366607                  Lucan

In [20]:
len(filtered_data)

3128

In [22]:
# Get the counts of each hotspot category
filtered_data['rec_tourist_spots_tag'].value_counts()

restaurant     1080
cafe           1035
pub             760
bar             150
theatre          41
arts_centre      27
cinema           21
nightclub        14
Name: rec_tourist_spots_tag, dtype: int64

In [23]:
# Create a map centered around Dublin
latitude = location[0]  # Latitude of the center point
longitude = location[1] # Longitude of the center point
map_osm = folium.Map(location=[latitude, longitude], zoom_start=12)
# icon = folium.Icon(icon='circle', prefix='fa', color='blue', icon_color='white', icon_size=(4, 4))

# Add markers for each charging station location
for index, spot in rec_tourist_spots.iterrows():
    name = spot['name']
    geometry = spot['geometry']

    # Extract latitude and longitude from the Polygon object
    if isinstance(geometry, Point):
        point = Point(geometry)
        lon = point.x
        lat = point.y
    else:
        centroid = geometry.centroid
        lon = centroid.x
        lat = centroid.y

    marker = folium.CircleMarker(location=[lat, lon], radius=4, popup=name, color='orange', fill=True, fill_color='orange')
    marker.add_to(map_osm)

# Display the map
map_osm